# Scraping data


In [5]:
from bs4 import BeautifulSoup 
import requests 
import pandas as pd

def get_listing_links(page_url):
    response = requests.get(page_url)
    soup = BeautifulSoup(response.content, 'html.parser')

    # Tìm tất cả các thẻ <h3 class="post-title"> rồi trích xuất href từ thẻ <a>
    listings = soup.select("h3.post-title a")  # Lấy tất cả các thẻ <a> trong <h3 class="post-title">
    
    listing_links = []
    for listing in listings:    
        link = listing['href']  # Lấy đường dẫn từ thuộc tính href
        full_link = f"https://phongtro123.com{link}"  # Thêm domain vào đường dẫn tương đối
        listing_links.append(full_link)
    
    return listing_links
    
def get_room_details(listing_url):
    response = requests.get(listing_url)
    soup = BeautifulSoup(response.content, 'html.parser')

    # 1. Tiêu đề và rating
    title_tag = soup.select_one("h1.page-h1 a")
    title = title_tag.get_text() if title_tag else 'N/A'
    
    rating_tag = soup.select_one("h1.page-h1 .star")
    rating = rating_tag.get('class')[1].split('-')[1] if rating_tag else 'N/A'  # Lấy số lượng sao từ class star-5
    
    # 2. Địa chỉ
    address_tag = soup.select_one("address.post-address")
    address = address_tag.get_text().replace("Địa chỉ:", "").strip() if address_tag else 'N/A'

    # 3. Giá
    price_tag = soup.select_one("div.item.price span")
    price = price_tag.get_text() if price_tag else 'N/A'

    # 4. Diện tích
    area_tag = soup.select_one("div.item.acreage span")
    area = area_tag.get_text().strip() if area_tag else 'N/A'

    # 5. ID phòng trọ
    id_tag = soup.select_one("div.item.hashtag span")
    room_id = id_tag.get_text() if id_tag else 'N/A'

    # 6. Thời gian đăng
    published_tag = soup.select_one("div.item.published span")
    published_time = published_tag['title'] if published_tag and 'title' in published_tag.attrs else 'N/A'

    # 7. Mô tả
    description_tag = soup.select_one("section.section.post-main-content div.section-content")
    description = description_tag.get_text(separator="\n").strip() if description_tag else 'N/A'
    
    # 8. Ngày hết hạn
    expiration_date_tag = soup.select_one("table.table tr:nth-child(8) td time")
    expiration_date = expiration_date_tag.get_text() if expiration_date_tag else 'N/A'

    # 9. Loại tin rao (lấy nội dung trong cột thứ 2)
    listing_type_tag = soup.select_one("tr:contains('Loại tin rao:') td:nth-child(2)")
    listing_type = listing_type_tag.get_text().strip() if listing_type_tag else 'N/A'

    # 10. Đối tượng thuê (lấy nội dung trong cột thứ 2)
    tenant_type_tag = soup.select_one("tr:contains('Đối tượng thuê:') td:nth-child(2)")
    tenant_type = tenant_type_tag.get_text().strip() if tenant_type_tag else 'N/A'


    # Trả về dictionary chứa tất cả các thông tin
    return {
        'room_id': room_id,
        'title': title,
        'address': address,
        'price': price,
        'area': area,
        'published_time': published_time,
        'expiration_date': expiration_date,   
        'listing_type': listing_type,         
        'tenant_type': tenant_type,
        'description': description           
    }

def scrape_all_pages(base_url, num_pages):
    all_links = []
    for page in range(1, num_pages + 1):
        page_url = f"{base_url}?page={page}" if page > 1 else base_url  # Tạo URL từng trang
        listing_links = get_listing_links(page_url)
        all_links.extend(listing_links)
        print(f"Đã lấy xong dữ liệu từ trang {page}")  # In ra để kiểm tra tiến trình
    return all_links

def scrape_all_listings(base_url, num_pages):
    # Lấy tất cả các đường dẫn bài đăng
    all_links = scrape_all_pages(base_url, num_pages)

    # Trích xuất thông tin từ từng bài đăng
    all_room_details = []
    for link in all_links:
        room_details = get_room_details(link)
        all_room_details.append(room_details)
        
    df = pd.DataFrame(all_room_details)
    
    return all_room_details



# Lấy url + số trang 


In [37]:
base_url = "https://phongtro123.com/tinh-thanh/ho-chi-minh"  # Trang chính
num_pages = 550  # Số lượng trang bạn muốn scraping
# Scraping dữ liệu từ nhiều trang
hcm_room_data = scrape_all_listings(base_url, num_pages) 


Đã lấy xong dữ liệu từ trang 1
Đã lấy xong dữ liệu từ trang 2
Đã lấy xong dữ liệu từ trang 3
Đã lấy xong dữ liệu từ trang 4
Đã lấy xong dữ liệu từ trang 5
Đã lấy xong dữ liệu từ trang 6
Đã lấy xong dữ liệu từ trang 7
Đã lấy xong dữ liệu từ trang 8
Đã lấy xong dữ liệu từ trang 9
Đã lấy xong dữ liệu từ trang 10
Đã lấy xong dữ liệu từ trang 11
Đã lấy xong dữ liệu từ trang 12
Đã lấy xong dữ liệu từ trang 13
Đã lấy xong dữ liệu từ trang 14
Đã lấy xong dữ liệu từ trang 15
Đã lấy xong dữ liệu từ trang 16
Đã lấy xong dữ liệu từ trang 17
Đã lấy xong dữ liệu từ trang 18
Đã lấy xong dữ liệu từ trang 19
Đã lấy xong dữ liệu từ trang 20
Đã lấy xong dữ liệu từ trang 21
Đã lấy xong dữ liệu từ trang 22
Đã lấy xong dữ liệu từ trang 23
Đã lấy xong dữ liệu từ trang 24
Đã lấy xong dữ liệu từ trang 25
Đã lấy xong dữ liệu từ trang 26
Đã lấy xong dữ liệu từ trang 27
Đã lấy xong dữ liệu từ trang 28
Đã lấy xong dữ liệu từ trang 29
Đã lấy xong dữ liệu từ trang 30
Đã lấy xong dữ liệu từ trang 31
Đã lấy xong dữ li

In [ ]:
df = pd.DataFrame(hcm_room_data)
df.info()
df.head(10)

In [39]:
import re
from underthesea import word_tokenize
from collections import Counter
# Đọc file stopwords
with open('vietnamese-stopwords.txt', 'r', encoding='utf-8') as f:
    vietnamese_stopwords = set(f.read().splitlines())

In [40]:
def preprocess_text(text):
    # Chuyển về chữ thường
    text = text.lower()
    # Xóa các ký tự đặc biệt và số
    text = re.sub(r'[^\w\s]', '', text)
    text = re.sub(r'\d+', '', text)
    # Tách từ
    words = word_tokenize(text)
    # Loại bỏ stopwords
    words = [word for word in words if word not in vietnamese_stopwords]
    return words

df['processed_description'] = df['description'].apply(preprocess_text)

# Tạo một list chứa tất cả các từ đã xử lý từ 10 dòng đầu
all_words = [word for words in df['processed_description'].head(10000) for word in words]

# Đếm tần suất của các từ
word_freq = Counter(all_words)

# In ra 20 từ xuất hiện nhiều nhất
print(word_freq.most_common(100))

# Các từ khóa chính cho mỗi cột
basic_amenities_keywords = [
    'tủ lạnh', 'bếp', 'máy lạnh', 'giường', 'nệm', 'bàn', 'ghế',
    'đầy đủ', 'máy giặt', 'máy', 'trang bị', 'tủ', 'tủ lạnh', 
    'cửa sổ', 'kệ', 'tiện nghi', 'vệ sinh'
    'gác', 'nội thất','bàn', 'nấu ăn', 'ban công'
]

security_keywords = [
    'khóa', 'khóa vân tay', 'camera', 'an ninh', 'bảo vệ', 'hệ thống an ninh', 'mật mã' ,"vân", "tay", "khóa điện tử"
]

parking_keywords = [
    'chỗ để xe', 'bãi đậu xe', 'nhà xe', 'bãi xe', 'hầm', 'gửi xe', 'xe'
]

elevator_keywords = [
    'thang máy'
]

laundry_area_keywords = [
    'sân', 'phơi', 'sân phơi'
]
internet_keywords = [
    'wifi', 'internet', 'mạng', 'free wifi'
]
university_keywords = [
    'trường', 'đại học', 'đh', 'trường học'
]

# Hàm xử lý tiện ích cơ bản
def extract_basic_amenities(text):
    found_keywords = [kw for kw in basic_amenities_keywords if kw in text]
    if 'tủ lạnh' in found_keywords or 'bếp' in found_keywords or 'máy lạnh' in found_keywords:
        if len(found_keywords) > 3:
            return ', '.join(found_keywords[:3]) + ', nội thất khác'
        else:
            return ', '.join(found_keywords)
    else:
        return 'không có thông tin'
    

def extract_security(text):
    found_keywords = [kw for kw in security_keywords if kw in text]
    
    # Nếu tìm thấy các từ liên quan đến "khóa điện tử", thêm vào kết quả "Khóa điện tử"
    if any(kw in text for kw in ['khóa', 'khóa vân tay', 'vân tay', 'mật mã', "vân", "tay", "khóa điện tử"]):
        found_keywords.append('Khóa điện tử')
    
    if found_keywords:
        return ', '.join(set(found_keywords))  # Sử dụng set để tránh lặp từ khóa
    else:
        return 'không có thông tin'
    

def extract_amenities_info(description):
    # Khởi tạo một danh sách rỗng để chứa các tiện ích tìm thấy
    parking_info = []

    # Kiểm tra từ khóa chỗ để xe
    if any(keyword in description for keyword in parking_keywords):
        parking_info.append("Chỗ để xe")
    
    # Kiểm tra từ khóa thang máy
    if any(keyword in description for keyword in elevator_keywords):
        parking_info.append("Thang máy")
    
    # Kiểm tra từ khóa sân phơi
    if any(keyword in description for keyword in laundry_area_keywords):
        parking_info.append("Sân phơi đồ")

    # Nếu không tìm thấy từ khóa nào, trả về "Không có thông tin"
    if not parking_info:
        return "Không có thông tin"
    
    # Trả về chuỗi kết quả tiện ích
    return ", ".join(parking_info)


# Hàm kiểm tra internet
def has_internet(text):
    return 'có' if any(kw in text for kw in internet_keywords) else 'Không'

# Hàm kiểm tra gần trường đại học
def near_university(text):
    return 'có' if any(kw in text for kw in university_keywords) else 'Không'

df['basic_amenities'] = df['processed_description'].apply(extract_basic_amenities)
df['security'] = df['processed_description'].apply(extract_security)
df['public_amenities'] = df['processed_description'].apply(extract_amenities_info)
df['has_internet'] = df['processed_description'].apply(has_internet)
df['near_university'] = df['processed_description'].apply(near_university)

df.head()
df.info()

[('phòng', 21966), ('giá', 7677), ('xe', 6432), ('an ninh', 5722), ('tự do', 5497), ('thuê', 5467), ('nội thất', 5302), ('tr', 5164), ('giờ giấc', 5058), ('m', 4978), ('liên hệ', 4934), ('máy lạnh', 4671), ('bếp', 4609), ('đường', 4238), ('chủ', 3675), ('khu', 3522), ('điện', 3444), ('đầy đủ', 3384), ('vân', 3288), ('chợ', 3265), ('đh', 3150), ('camera', 3054), ('cửa sổ', 3052), ('máy', 3006), ('đi', 2988), ('trọ', 2926), ('tiện ích', 2837), ('tủ', 2765), ('k', 2746), ('thoáng', 2740), ('thuận tiện', 2685), ('q', 2576), ('địa chỉ', 2558), ('rộng', 2487), ('tủ lạnh', 2481), ('đại học', 2447), ('khu vực', 2442), ('rộng rãi', 2419), ('thang máy', 2413), ('full', 2384), ('p', 2317), ('miễn phí', 2280), ('trường', 2277), ('di chuyển', 2226), ('sạch sẽ', 2196), ('trung tâm', 2179), ('phường', 2151), ('gác', 2146), ('kệ', 2142), ('wifi', 2070), ('mát', 2069), ('giặt', 1907), ('căn hộ', 1903), ('quần áo', 1880), ('tư vấn', 1862), ('dịch vụ', 1819), ('diện tích', 1731), ('máy giặt', 1725), ('bả

In [42]:
import pyodbc

# Thông tin kết nối đến Azure SQL Database
server = 'hfproject.database.windows.net'
database = 'G1_QTCSDL'
username = 'hfproject'
password = 'Hfan8338#'  
driver = '{ODBC Driver 18 for SQL Server}'

# Tạo kết nối đến Azure SQL Database
conn = pyodbc.connect(
    'DRIVER=' + driver + ';SERVER=' + server + ';DATABASE=' + database + ';UID=' + username + 
    ';PWD=' + password + ';Encrypt=yes;TrustServerCertificate=no;Connection Timeout=30'
)

# Tạo cursor để thực hiện truy vấn
cursor = conn.cursor()

print("Kết nối thành công với Azure SQL Database!")

# Bước 1: Tạo bảng (nếu chưa có)
create_table_query = """
CREATE TABLE listings (room_id NVARCHAR(255), title NVARCHAR(255),
                       address NVARCHAR(255), price NVARCHAR(50),
                       area NVARCHAR(50), published_time NVARCHAR(50),
                       expiration_date NVARCHAR(50), listing_type NVARCHAR(50),
                       tenant_type NVARCHAR(50), basic_amenities NVARCHAR(50),
                       security NVARCHAR(100), public_amenities NVARCHAR(50),
                       has_internet NVARCHAR(50), near_university NVARCHAR(50));
                    """

# Thực hiện câu lệnh SQL để tạo bảng
try:
    cursor.execute(create_table_query)
    print("Bảng đã được tạo thành công.")
except pyodbc.ProgrammingError as e:
    # Nếu bảng đã tồn tại, có thể bỏ qua lỗi này
    print("Bảng có thể đã tồn tại. Bỏ qua bước tạo bảng.")

# Đảm bảo con trỏ vẫn mở trước khi chèn dữ liệu
try:
    # Bước 2: Chèn dữ liệu từ DataFrame vào bảng listings
    for index, row in df.iterrows():
        cursor.execute("""
            INSERT INTO listings (room_id, title, address, price, area,
                                  published_time, expiration_date, listing_type,
                                  tenant_type, basic_amenities, security, 
                                  public_amenities, has_internet, near_university) 
            VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
        """, 
        row['room_id'], row['title'], row['address'], row['price'], row['area'], 
        row['published_time'],row['expiration_date'], row['listing_type'],
        row['tenant_type'],  row['basic_amenities'], row['security'],
        row['public_amenities'], row['has_internet'], row['near_university'])
    
    # Lưu thay đổi vào cơ sở dữ liệu
    conn.commit()
    print("Dữ liệu đã được chèn thành công.")

    # Kiểm tra dữ liệu đã được chèn vào bảng hay chưa
    cursor.execute("SELECT * FROM listings")
    rows = cursor.fetchall()
    if len(rows) > 0:
        print("Dữ liệu đã được chèn vào bảng listings:")
        for row in rows:
            print(row)
    else: 
        print("Bảng listings trống.")

except pyodbc.ProgrammingError as e:
    print(f"Lỗi xảy ra: {e}")

finally:
    # Đóng con trỏ và kết nối sau khi hoàn tất các thao tác
    cursor.close()
    conn.close()

Kết nối thành công với Azure SQL Database!
Bảng đã được tạo thành công.
Dữ liệu đã được chèn thành công.
Dữ liệu đã được chèn vào bảng listings:
('665858', 'Chính chủ cho thuê phòng trọ mới đẹp tại 493A/188 Cách Mạng Tháng Tám, Phường 13, Quận 10', '493A/188 Cách Mạng Tháng Tám, Phường 13, Quận 10, Hồ Chí Minh', '4 triệu/tháng', '25m2', 'Thứ 5, 08:53 03/10/2024', 'Thứ 5, 08:53 10/10/2024', 'Phòng trọ, nhà trọ', 'Tất cả', 'bếp, máy lạnh', 'không có thông tin', 'Không có thông tin', 'Không', 'Không')
('665859', 'Chi 3,5 tr cho 2 người ở tại căn hộ mini 25m2 đầy đủ tiện nghi, nấu ăn trong phòng, không gian thoáng mát, cửa sổ rộng', 'Hẻm 839 Lê Văn Lương, Quận 7, Hồ Chí Minh', '3.5 triệu/tháng', '25m2', 'Thứ 5, 08:45 03/10/2024', 'Thứ 5, 08:45 10/10/2024', 'Phòng trọ, nhà trọ', 'Tất cả', 'bếp, máy lạnh, đầy đủ, nội thất khác', 'an ninh, camera', 'Chỗ để xe, Thang máy', 'có', 'có')
('649687', 'GẦN TRƯỜNG GTVT, NGOẠI THƯƠNG, HUTECH, HỒNG BÀNG, UEF - AN NINH, TIỆN NGHI - TT Q.BÌNH THẠNH ĐƯỜNG